In [1]:
from netgen.meshing import *
from netgen.csg import *

from ngsolve import ngsglobals

# Define two bricks, partially intersecting each other
#
#         +++++++ 
#         +     +
#    #####*#####*#####
#    #    +     +    #
#    #    +++++++    #
#    #               #
#    #               #
#    #               #
#    #               #
#    #################
#
# The meshes should be seperated from each other.
#
# Goal: Calculate contact forces, for the smaller brick beeing fixed
#       on the upper surface and the larger brick beeing fixed on the 
#       lower surface.
#
#




# Variable for the intersection of the bricks
delta=-0.1


# Create Brick1
geo1 = CSGeometry()

left  = Plane (Pnt(0,0,0), Vec(-1,0,0) ).bc('left_1')
right = Plane (Pnt(1,1,1), Vec( 1,0,0) ).bc('right_1')
front = Plane (Pnt(0,0,0), Vec(0,-1,0) ).bc('front_1')
back  = Plane (Pnt(1,1,1), Vec(0, 1,0) ).bc('back_1')
bot   = Plane (Pnt(0,0,0), Vec(0,0,-1) ).bc('bottom_1')
top   = Plane (Pnt(1,1,1), Vec(0,0, 1) ).bc('top_1')

brick_1 = left * right * front * back * bot * top

geo1.Add(brick_1,maxh=0.2)
m1 = geo1.GenerateMesh()


# Create Brick2
geo2 = CSGeometry()

left  = Plane (Pnt(.25,.25,1+delta), Vec(-1,0,0) ).bc('left_1')
right = Plane (Pnt(.75,.75,1.5+delta), Vec( 1,0,0) ).bc('right_1')
front = Plane (Pnt(.25,.25,1+delta), Vec(0,-1,0) ).bc('front_1')
back  = Plane (Pnt(.75,.75,1.5+delta), Vec(0, 1,0) ).bc('back_1')
bot   = Plane (Pnt(.25,.25,1+delta), Vec(0,0,-1) ).bc('bottom_1')
top   = Plane (Pnt(.75,.75,1.5+delta), Vec(0,0, 1) ).bc('top_1')

brick_2 = left * right * front * back * bot * top

geo2.Add(brick_2,maxh=0.1)
m2 = geo2.GenerateMesh()



print ("***************************")
print ("** merging suface meshes **")
print ("***************************")

# create an empty mesh
mesh = Mesh()

# a face-descriptor stores properties associated with a set of surface elements
# bc .. boundary condition marker,
# domin/domout .. domain-number in front/back of surface elements (0 = void),
# surfnr .. number of the surface described by the face-descriptor

fd_outside = mesh.Add (FaceDescriptor(bc=1,domin=1,surfnr=1))
fd_inside = mesh.Add (FaceDescriptor(bc=2,domin=2,domout=1,surfnr=2))
# copy all boundary points from first mesh to new mesh.
# pmap1 maps point-numbers from old to new mesh

pmap1 = { }
for e in m1.Elements2D():
    for v in e.vertices:
        if (v not in pmap1):
            pmap1[v] = mesh.Add (m1[v])


# copy surface elements from first mesh to new mesh
# we have to map point-numbers:

for e in m1.Elements2D():
    mesh.Add (Element2D (fd_outside, [pmap1[v] for v in e.vertices]))



# same for the second mesh:

pmap2 = { }
for e in m2.Elements2D():
    for v in e.vertices:
        if (v not in pmap2):
            pmap2[v] = mesh.Add (m2[v])

for e in m2.Elements2D():
    mesh.Add (Element2D (fd_inside, [pmap2[v] for v in e.vertices]))


print ("******************")
print ("** merging done **")
print ("******************")


mesh.GenerateVolumeMesh()


mesh = Mesh(ngmesh)
mesh.GetBoundaries()

Draw(mesh)

***************************
** merging suface meshes **
***************************
******************
** merging done **
******************


NgException: Stop meshing since boundary mesh is overlapping